In [4]:
from time import monotonic
from sys import path
from os import getenv
path.append(getenv("HOME") + "/projects/travnik")
from travnik import glob
print("......")
start = monotonic()
torrents = glob("/mnt/slu/a/arhiv/travnik/2024b")
print(len(torrents), "@", monotonic()-start, "s")
# t = Torrent()
# t.file("/root/projects/travnik/449a38ef7e042bd2d75e8921aa02f6f244165d9d.torrent")
# print(t.sha1.hex())
# for path, length in t.paths():
#     print(path, length)
# print(t)

......
fixed bad single file torrent 7c21c72cb8eab60298eeea51bf212548b41590ce
8212 @ 47.7344050409738 s


In [5]:
from travnik import Type
for hash, torrent in torrents.items():
    if torrent.type == Type.HYBRID and not torrent.dict.get(b'info').get(b'meta version'):
        print(torrent.sha1.hex(), torrent.sha256.hex())
print("...")

...


In [6]:
s = monotonic()
prej = None
skup = 0
dat = 0
vel = 0
for torrent in sorted([torrent for sha1, torrent in torrents.items()], key=lambda x:x.dict.get(b'creation date')):
    č = torrent.dict.get(b'creation date')
    dat += sum(1 for path, size in torrent.paths())
    vel += sum(size for path, size in torrent.paths())
    if not prej:
        prej = č
        continue
    if prej + 60*10 > č:
        skup += č-prej
    prej = č
print(monotonic()-s, "torrenti so se zbirali", skup/86400, "dni. en torrent je bil najden v povprečju na", skup/len(torrents), "sekund, v", len(torrents), "so metapodatki", dat, "datotek", "v skupni velikosti", vel/(1024**4), "TiB")

0.5483028320013545 torrenti so se zbirali 0.7585995370370371 dni. en torrent je bil najden v povprečju na 7.981368728689723 sekund, v 8212 so metapodatki 397833 datotek v skupni velikosti 44.76920055183473 TiB


In [7]:
s = monotonic()
def uas(normalize=True, minrepr=0):
    odjemalci = {}
    for sha1, torrent in torrents.items():
        odjemalec = torrent.dict.get(b'source').get(b'v')
        if normalize and odjemalec is not None:
            if b'/' in odjemalec:
                odjemalec = odjemalec.split(b'/')[0]
            elif b' (' in odjemalec:
                odjemalec = odjemalec.split(b' (')[0]
            else:
                odjemalec = odjemalec.split(b' ')[0]
            odjemalec = odjemalec.replace(b'\xc2\xb5', b'\xce\xbc').decode()
        if odjemalec not in odjemalci.keys():
            odjemalci[odjemalec] = 1
        else:
            odjemalci[odjemalec] += 1
    trueodj = {"ostali": 0}
    count = 0
    for key, value in odjemalci.items():
        count += 1
        if value < minrepr:
            trueodj["ostali"] += value
        else:
            trueodj[key] = value
    trueodj = [(v, k) for k, v in trueodj.items()]
    return trueodj, count
odjemalci, count = uas(True, minrepr=0.01*len(torrents))
odjemalci = sorted(odjemalci, reverse=False)
from matplotlib import pyplot
%matplotlib notebook
fig, axes = pyplot.subplots()
from math import log
# axes.pie([log(sights) if sights else 0 for sights, name in odjemalci], labels=[name for sights, name in odjemalci])
axes.barh([name if name is not None else "neznan" for sights, name in odjemalci], [sights for sights, name in odjemalci])
axes.set_title("log skala odjemalcev")
pyplot.xscale("log")
fig.show()
print(monotonic()-s, "za", count, "različnih odjemalcev")

<IPython.core.display.Javascript object>

6.861141365981894 za 54 različnih odjemalcev


In [8]:
s = monotonic()
keys = {}
for sha1, torrent in torrents.items():
    for key in torrent.dict.get(b'info').keys():
        if key.decode() not in keys.keys():
            value = torrent.dict.get(b'info').get(key)
            if type(value) is bytes:
                try:
                    value = value.decode()
                except UnicodeDecodeError:
                    pass
            keys[key.decode()] = [1, value, sha1.hex()]
        else:
            keys[key.decode()][0] += 1
sort = sorted(keys, key=lambda x: keys[x][0])
print(monotonic()-s, "s", len(keys))
%matplotlib notebook
fig, ax = pyplot.subplots();
ax.barh(sort, [keys[x][0] for x in sort])
pyplot.xscale("log")
pyplot.xlabel("število pojavitev ključa v slovarju info")
fig.show() ## TODO komentiraj
for i in sort:
    print(i, keys[i])

0.02595838499837555 s 31


<IPython.core.display.Javascript object>

nnm-club_cool [1, 1, 'b0371a6f71bb5e03b12e91d041aaff27dc521299']
x-amz-bucket [1, 'biglybt-files', '6b595d27461dd22a922fb503180c273d903e88cd']
x-amz-key [1, 'plugins/vuzexcode-win32_2.3.2.zip', '6b595d27461dd22a922fb503180c273d903e88cd']
可爱的图图 [1, 'https://www.baidu.com', '7c306fd27cde40bf1abcebf8bbda7072117555d3']
unique [1, 'do7ak59tniya4gypkgeap2oj1eby4ttwmds', 'c1647873f77b5250eef8c7eb691c954dae8bea18']
zzzza1111sqdxsd [1, 'a', '5a7f6183614e25bbb4150007efd13c6162f181a4']
tracker [3, '', 'baea7731fc449003136540f5c092bf9eb748e4b5']
md5sum [3, b'5\x87\xe9~\xa2?\xec\x13\x18\x868\x9f\xacz*\xd4', 'b0a9855e0a63d07c933761b42d4ae3a26d9a31a5']
comment [3, 'Torrent downloaded from torrent cache at http://torcache.net/', '0d049cf667e09e2872b959d630ddb0fa935d376b']
attr [4, 'x', '42e45403f219c1a7f7c30012af0c69eb3d48254b']
cross_seed_entry [4, '3af43f7c81ced9b5d41fdc3c91a5d3f0', '353eac52c1c1e58a17752473e2bd58210c6d1d6a']
creation date [9, 1458498339, '0d049cf667e09e2872b959d630ddb0fa935d376b']


In [9]:
s = monotonic()
def removeminorities(population, minrepr=0, ostalo="ostalo"):
    true = {ostalo: 0}
    for key, value in population.items():
        if value < minrepr:
            true[ostalo] += value
        else:
            true[key] = value
    return true
def sources():
    sources = {}
    for sha1, torrent in torrents.items():
        source = torrent.dict.get(b'info').get(b'source')
        if source is None:
            source = torrent.dict.get(b'info').get(b'publisher')
        if source is None:
            source = torrent.dict.get(b'info').get(b'publisher-url')
        if source is None:
            source = torrent.dict.get(b'info').get(b'comment')
        try:
            if type(source) is bytes:
                source = source.decode().strip()
        except UnicodeDecodeError:
            pass
        if source not in sources.keys():
            sources[source] = 1
        else:
            sources[source] += 1
    return sources
sources = sources()
sources = removeminorities(sources, len(sources)*0, "ostali")
sort = sorted(sources, reverse=True, key=lambda x:sources[x])
sort.remove(None)
print(monotonic()-s, "s", sources[None]/len(torrents)*100, "brez ključa source, publisher, publisher-url ali comment", len(sources), "virov")
%matplotlib notebook
fig, ax = pyplot.subplots();
ax.barh([str(x) for x in sort], [sources[x] for x in sort])
pyplot.xscale("log")
pyplot.xlabel("število pojavitev distributerja")
fig.show() ## TODO komentiraj
from tabulate import tabulate
tabulate([[x, sources[x]] for x in sort], tablefmt="html")
for x in sort:
    print(sources[x], "\t", x)

0.03974157400080003 s 93.9965903555772 brez ključa source, publisher, publisher-url ali comment 237 virov


<IPython.core.display.Javascript object>

25 	 PMEDIA
25 	 LostFilm.TV
15 	 -
15 	 脫拉庫
13 	 第一會所新片@SIS001
13 	 Zamunda.NET
12 	 
12 	 http://tapochek.net/index.php
11 	 1024社區最新地址
10 	 2048
10 	 小隻馬
8 	 灣搭拉咩拉
7 	 麻豆之神
6 	 高清下载吧！
6 	 RV原创
6 	 https://FreeCourseWeb.com
5 	 1024核工厂
5 	 2048核基地
4 	 Zelka.ORG
4 	 老含及
4 	 小樱
4 	 1024
4 	 nyaa.si
4 	 天天新鮮
4 	 ~@~江~南~@~
4 	 吃雞大神
4 	 [animelayer.ru] Animelayer
4 	 1024社區
3 	 47BT
3 	 https://crackshash.com/
3 	 b'\xab\xb0\xa5\xab\xad\xb7\xb1\xa1~\xa4p\xb9t\xad\xec\xb3\xd0'
3 	 第一會所新片
3 	 國產精品
3 	 xue0117
3 	 最新资源发布站
3 	 鱼香肉丝
3 	 [http://biboboon.name] BaibaKo.TV
3 	 https://hjd.tw
3 	 olo
2 	 RedLineSP - http://redlinesp.org/newrlsp/index.php
2 	 [http://rudub.net] RuDub.TV
2 	 https://discord.gg/vbJ7RTn
2 	 杏吧论坛
2 	 nyaa001
2 	 NikeのＢ@第一会所
2 	 Accidentaccio
2 	 愛在黑夜001
2 	 ? nike ?
2 	 b48t.com
2 	 易破解网站
2 	 XIU
2 	 dioguitar23.co(第六天魔王)@最新AV海量免費播放~魔王在線
2 	 RZK
2 	 Weagogo
2 	 CMCT团队荣誉出品
2 	 发发发
2 	 PB
2 	 0
2 	 [http://x-torrents.org] X-Torrents.org
1 	 上善若水@www.sexinsex.net
1 	 最新の欧

In [10]:
s = monotonic()
from mimetypes import guess_type
def ext(mime=False, minreprratio=0):
    bycount = {}
    bysize = {}
    bysizerepresentative = {}
    filescount = 0
    bytescount = 0
    for sha1, torrent in torrents.items():
        try:
            representatives = {}
            for path, size in torrent.paths():
                filescount += 1
                bytescount += size
                if mime:
                    ext = guess_type(path.pop().decode(encoding="iso-8859-2"))[0]
                else:
                    ext = path.pop().split(b'.').pop().decode(encoding="iso-8859-2").lower()
                if ext not in bycount.keys():
                    bycount[ext] = 1
                else:
                    bycount[ext] += 1
                if ext not in bysize.keys():
                    bysize[ext] = size
                else:
                    bysize[ext] += size
                if ext not in representatives.keys():
                    representatives[ext] = size
                else:
                    representatives[ext] += size
        except AttributeError:
            print(sha1.hex(), torrent)
            raise AttributeError
        try:
            representative = sorted(representatives, key=lambda x:representatives[x]).pop()
        except IndexError:
            print(sha1.hex(), torrent)
            raise IndexError
        if representative not in bysizerepresentative.keys():
            bysizerepresentative[representative] = 1
        else:
            bysizerepresentative[representative] += 1
    truebycount = removeminorities(bycount, minreprratio*filescount, "ostale")
    truebysize = removeminorities(bysize, minreprratio*bytescount, "ostale")
    truebysizerepresentative = removeminorities(bysizerepresentative, minreprratio*len(torrents), "ostale")
    for data in [truebycount, truebysize, truebysizerepresentative]:
        data = [(v, k) for k, v in data.items()]
    return truebycount, truebysize, truebysizerepresentative, len(bycount), filescount, bytescount
print("...")
bycount, bysize, bysizerepresentative, kinds, filescount, bytescount = ext(False, 0.001)
print(monotonic()-s, "s", kinds, "različnih tipov v", filescount, "datotekah in", bytescount/(1024**4), "TiB")

...
1.3386651040054858 s 60942 različnih tipov v 397833 datotekah in 44.76920055183473 TiB


In [13]:
sortcount = sorted(bycount, reverse=False, key=lambda x: bycount[x])
sortsize = sorted(bysize, reverse=False, key=lambda x: bysize[x])
sortsizerepresentative = sorted(bysizerepresentative, reverse=False, key=lambda x: bysizerepresentative[x])
from matplotlib import pyplot
%matplotlib notebook
for desc, data in {"po številu datotek": (sortcount, bycount), "po velikosti datotek": (sortsize, bysize), "po številu po velikosti največjih datotek torrentov": (sortsizerepresentative, bysizerepresentative)}.items():
    fig, axes = pyplot.subplots()
    # axes.pie([data[1][key] for key in data[0]], labels=data[0])
    axes.barh(data[0], [data[1][key] for key in data[0]])
    pyplot.xscale("log")
    axes.set_title(desc)
    fig.show()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>